In [1]:
from cimloader.databases import ConnectionInterface, ConnectionParameters, Parameter, QueryResponse
from cimloader.databases.mysql import MySQL

In [2]:
params = ConnectionParameters(host= "localhost", database="rc4_2021", username="root", password="password", cim_profile='rc4_2021', namespace="http://iec.ch/TC57/CIM100#")
mysql = MySQL(params)

In [3]:
mysql.configure()

Unable to create table for class DateInterval
Unable to create table for class DecimalQuantity
Unable to create table for class Limit
Unable to create table for class MonthDayInterval
Unable to create table for class Procedure
Unable to create table for class StateVariable


In [4]:
import importlib
cim_profile = 'rc4_2021'
cim = importlib.import_module('cimgraph.data_profile.' + cim_profile)

In [5]:
from cimgraph.databases import Parameter, ConnectionParameters
from cimgraph.databases.blazegraph.blazegraph import BlazegraphConnection
from cimgraph.models import FeederModel
import json
import time
# Blazegraph connection for running outside the container
params = ConnectionParameters(url = "http://localhost:8889/bigdata/namespace/kb/sparql", cim_profile='rc4_2021')
bg = BlazegraphConnection(params, 'rc4_2021')


#feeder_mrid = "_C1C3E687-6FFD-C753-582B-632A27E28507"  # 123 bus
# feeder_mrid = "_49AD8E07-3BF9-A4E2-CB8F-C3722F837B62"  # 13 bus
# feeder_mrid = "5B816B93-7A5F-B64C-8460-47C17D6E4B0F" # 13 bus asets
# feeder_mrid = "_4F76A5F9-271D-9EB8-5E31-AA362D86F2C3"  # 8500 node
#feeder_mrid = "_67AB291F-DCCD-31B7-B499-338206B9828F" # J1
#feeder_mrid = "_9CE150A8-8CC5-A0F9-B67E-BBD8C79D3095"  # R2 12.47 3
feeder_mrid = "_EE71F6C9-56F0-4167-A14E-7F4C71F10EAA" #9500 node
## Create Distributed CIM Model:
feeder = cim.Feeder(mRID=feeder_mrid)
start = time.perf_counter()
network_bg = FeederModel(connection=bg, container=feeder, distributed=False, cim_profile = 'rc4_2021')
build_time = time.perf_counter() - start
print("blazegraph init time:", build_time)


cim_class = cim.ACLineSegment
start = time.perf_counter()
network_bg.get_all_edges(cim_class)
build_time = time.perf_counter() - start
print("blazegraph query time for", len(network_bg.graph[cim_class]), "objects:", build_time)

blazegraph init time: 0.3652731969996239
blazegraph query time for 3909 objects: 2.588196913999127


In [6]:
mysql.upload_from_cimgraph(network_bg)

In [7]:
start = time.perf_counter()
myresult = mysql.execute("SELECT * FROM ACLineSegment")


for x in myresult:
    print(x)
build_time = time.perf_counter() - start
print("mysql query time:", build_time)

('_0A1B9817-023D-43F3-A599-D975C7B47EE5', None, None, 'cap_2b', None, None, None, None, None, '{"@id": "_462765A4-1AA9-404F-AD43-72A97F420CC3", "@type": "Location"}', '["{\\"@type\\": \\"Analog\\", \\"@id\\": \\"_8475cd7d-50ce-489b-9ffb-d514eff253bd\\"}", "{\\"@type\\": \\"Analog\\", \\"@id\\": \\"_cb115988-0d32-4ca3-ace9-d49ddf8780ad\\"}"]', None, None, None, None, None, None, None, None, '{"@id": "_EE71F6C9-56F0-4167-A14E-7F4C71F10EAA", "@type": "Feeder"}', None, None, None, '{"@id": "_9D8652E0-A64E-4333-BE4D-9221C40E469E", "@type": "BaseVoltage"}', None, '["{\\"@type\\": \\"Terminal\\", \\"@id\\": \\"_C3F6A5FB-D000-487F-95FA-11318BBF3B84\\"}", "{\\"@type\\": \\"Terminal\\", \\"@id\\": \\"_5B8CB4DC-5499-4DD8-AC23-1B16C59CC907\\"}"]', 0.001, None, None, None, None, None, None, None, None, None, '["{\\"@type\\": \\"ACLineSegmentPhase\\", \\"@id\\": \\"_CB6D7BF4-71D0-4958-8764-523C868B797A\\"}"]', None, None, None, None, '{"@id": "_A6A2C78A-79B8-481B-826C-37C0289D69BE", "@type": "PerLen